In [2]:
pip install pandas numpy shap sklearn ta lime

     |████████████████████████████████| 358kB 4.1MB/s 
     |████████████████████████████████| 276kB 37.1MB/s 
  Created wheel for shap: filename=shap-0.39.0-cp37-cp37m-linux_x86_64.whl size=491619 sha256=bcf5f8e528245cfa936bc537408ede1efa9c1018ac0a0af6b2fe35cd3d60c5a5
  Stored in directory: /root/.cache/pip/wheels/15/27/f5/a8ab9da52fd159aae6477b5ede6eaaec69fd130fa0fa59f283
  Created wheel for ta: filename=ta-0.7.0-cp37-none-any.whl size=28716 sha256=dc83ef401724c7cdd0d097a39d2141c2e8fa6b53345fc4320613465f0828e1fe
  Stored in directory: /root/.cache/pip/wheels/dd/88/30/de9553fb54a474eb7480b937cdbb140bdda613d29cf4da7994
  Created wheel for lime: filename=lime-0.2.0.1-cp37-none-any.whl size=283858 sha256=5627b5f91738597754714556a467712bb4140f60dfa0eb7e2027628239def97b
  Stored in directory: /root/.cache/pip/wheels/4c/4f/a5/0bc765457bd41378bf3ce8d17d7495369d6e7ca3b712c60c89
Successfully built shap ta lime


In [1]:
import pandas as pd
import numpy as np
import shap
from sklearn.metrics import accuracy_score as acc
from sklearn.metrics import precision_score as prec
from sklearn.neural_network import MLPClassifier
from time import time
from ta.utils import dropna
from ta.volatility import DonchianChannel as DC
from ta.volatility import KeltnerChannel as KC
from ta.volatility import BollingerBands as BB
from datetime import datetime, timedelta

data = pd.read_csv('data.csv', sep='\t')
data.head()

DATE      TIME    OPEN    HIGH     LOW   CLOSE  TICKVOL    VOL  SPREAD
0  2019.12.09  09:00:00  110930  111000  110910  110990     3447  11586       5
1  2019.12.09  09:01:00  110990  111125  110975  111075     9410  36048       5
2  2019.12.09  09:02:00  111080  111185  111080  111180     5629  22859       5
3  2019.12.09  09:03:00  111180  111185  111125  111175     3795  15209       5
4  2019.12.09  09:04:00  111180  111215  111165  111205     3308  11132       5

In [2]:
# Método de separação dos dados de Treino e Teste. Sem alterações comparado ao apresentado no exemplo
def split_treino_test(data):
    train = data[data['datetime'] < '2020-07-01']
    teste = data[data['datetime'] >= '2020-07-01']
    return train, teste

In [3]:
# Tratamentos básicos de datas. Sem alterações comparado ao apresentado no exemplo
data['datetime'] = data['DATE'] + ' ' + data['TIME']
data['datetime'] = pd.to_datetime(data['datetime'])
data.sort_values(by = 'datetime', inplace = True)

# Novas features baseadas em indicadores de volatilidade
# 1 - Donchian Channel Percentage Band (precisa do HIGH, LOW e CLOSE)
# 2 - Keltner Channel Percentage Band (precisa do HIGH, LOW e CLOSE)
# 3 - Bollinger Channel Percentage Band (precisa do CLOSE)
data = data[['datetime', 'HIGH', 'LOW', 'TICKVOL', 'CLOSE']]

# Renomeando coluna. Sem alterações comparado ao apresentado no exemplo
data.rename(columns = {'CLOSE':'valor'}, inplace = True)
data.loc[:,'target_num'] = data['valor'].shift(-1)
data.loc[:,'target_diff'] = data['target_num']  - data['valor']
data.loc[:,'target'] = data['target_diff'].apply(lambda x: 1 if x>=10 else 0)
data = data.drop(columns = ['target_num', 'target_diff'])

data.head()

datetime    HIGH     LOW  TICKVOL   valor  target
0 2019-12-09 09:00:00  111000  110910     3447  110990       1
1 2019-12-09 09:01:00  111125  110975     9410  111075       1
2 2019-12-09 09:02:00  111185  111080     5629  111180       0
3 2019-12-09 09:03:00  111185  111125     3795  111175       1
4 2019-12-09 09:04:00  111215  111165     3308  111205       0

In [4]:
# remover primeira linha do dia.
# Outra opção seria deixar estas linhas e manter a feature primeira_do_dia,
# para informar que aquele ponto pode estar sujeito a mais oscilações.
# Esta estratégia não é ideal no caso do uso de modelos lineares

data['primeira_do_dia'] = data['datetime'].diff() > pd.Timedelta(10, unit = 'hour')
data = data.loc[data['primeira_do_dia'] == False]
data = data[['datetime', 'valor', 'TICKVOL', 'HIGH', 'LOW', 'target']].reset_index(drop = True)
data.head()

datetime   valor  TICKVOL    HIGH     LOW  target
0 2019-12-09 09:00:00  110990     3447  111000  110910       1
1 2019-12-09 09:01:00  111075     9410  111125  110975       1
2 2019-12-09 09:02:00  111180     5629  111185  111080       0
3 2019-12-09 09:03:00  111175     3795  111185  111125       1
4 2019-12-09 09:04:00  111205     3308  111215  111165       0

In [5]:
# Novas features calculadas a partir dos indicadores Donchian Channel, Keltner Channele e Bollinger Band
data_novas_features = data.copy()
data_novas_features['porcent_dc'] = DC(
    high=data_novas_features['HIGH'], low=data_novas_features['LOW'], close=data_novas_features['valor']
).donchian_channel_pband()
data_novas_features['porcent_kc'] = KC(
    high=data_novas_features['HIGH'], low=data_novas_features['LOW'], close=data_novas_features['valor']
).keltner_channel_pband()
data_novas_features['porcent_bb'] = BB(close=data_novas_features['valor']).bollinger_pband()

data_novas_features = data_novas_features.dropna()
data_novas_features.reset_index(drop = True, inplace = True)
data_novas_features.head()

datetime   valor  TICKVOL  ...  porcent_dc  porcent_kc  porcent_bb
0 2019-12-09 09:19:00  111255     2992  ...    0.971831    1.198413    0.734259
1 2019-12-09 09:20:00  111255     1895  ...    0.965517    1.089015    0.765122
2 2019-12-09 09:21:00  111225     1945  ...    0.783784    0.673203    0.569301
3 2019-12-09 09:22:00  111215     1931  ...    0.642857    0.496324    0.472465
4 2019-12-09 09:23:00  111230     1544  ...    0.720000    0.679487    0.580744

[5 rows x 9 columns]

In [6]:
data_novas_features = data_novas_features[
    ['datetime', 'porcent_dc', 'porcent_kc', 'porcent_bb', 'valor', 'TICKVOL','target']].reset_index(drop = True)

data_novas_features.head()

datetime  porcent_dc  porcent_kc  ...   valor  TICKVOL  target
0 2019-12-09 09:19:00    0.971831    1.198413  ...  111255     2992       0
1 2019-12-09 09:20:00    0.965517    1.089015  ...  111255     1895       0
2 2019-12-09 09:21:00    0.783784    0.673203  ...  111225     1945       0
3 2019-12-09 09:22:00    0.642857    0.496324  ...  111215     1931       1
4 2019-12-09 09:23:00    0.720000    0.679487  ...  111230     1544       0

[5 rows x 7 columns]

In [7]:
# criando variaveis lagadas
# 3 valores lagados no tempo e 3 diferenças de valores lagados
data_final = data_novas_features.copy()

data_final['valor_l1'] = data_final['valor'].shift(1)
data_final['valor_l2'] = data_final['valor'].shift(2)
data_final['valor_l3'] = data_final['valor'].shift(3)

data_final['diff_l1'] = data_final['valor']  - data_final['valor_l1']
data_final['diff_l2'] = data_final['valor']  - data_final['valor_l2']
data_final['diff_l3'] = data_final['valor']  - data_final['valor_l3']

data_final = data_final.dropna()
data_final.reset_index(drop = True, inplace = True)
data_final.head()

datetime  porcent_dc  porcent_kc  ...  diff_l1  diff_l2  diff_l3
0 2019-12-09 09:22:00    0.642857    0.496324  ...    -10.0    -40.0    -40.0
1 2019-12-09 09:23:00    0.720000    0.679487  ...     15.0      5.0    -25.0
2 2019-12-09 09:24:00    0.680000    0.586022  ...     -5.0     10.0      0.0
3 2019-12-09 09:25:00    0.600000    0.381159  ...    -10.0    -15.0      0.0
4 2019-12-09 09:26:00    0.695652    0.586257  ...     15.0      5.0      0.0

[5 rows x 13 columns]

In [8]:
# Separação dos dados de treino e teste
treino, teste = split_treino_test(data_final)
X_treino = treino.copy().drop(columns = ['target', 'datetime'])
X_teste = teste.copy().drop(columns = ['target', 'datetime'])

y_treino = treino[['target']]
y_teste = teste[['target']]

In [9]:
# Montando camadas das redes neurais
qtd_atr = X_treino.shape[1] - 1
qtd_neuronios = [n for n in range(qtd_atr, (qtd_atr*2)+1, 3)]
qtd_neuronios.append(0)

camadas = []
for c1 in qtd_neuronios:
    for c2 in qtd_neuronios:
        for c3 in qtd_neuronios:
            if c2 == 0 or c3 == 0:
                continue
            elif c1 == 0:
                camadas.append((c2, c3))
            if c1 != 0 and c2 != 0 and c3 != 0:
                camadas.append((c1, c2, c3))

print(f"Quantidades de combinações de camadas: {len(camadas)}")

Quantidades de combinações de camadas: 80


In [11]:
# Montando as redes neurais
redes = []
for hidden_layer_sizes in camadas:
    for activation in ['logistic', 'relu']:
        for solver in ['sgd', 'adam']:
          for learning_rate_init in [0.01, 0.001, 0.0001]:
            if solver == 'sgd':
                redes.append(
                    MLPClassifier(
                        hidden_layer_sizes=hidden_layer_sizes, activation=activation, solver=solver,
                        learning_rate='adaptive', learning_rate_init=learning_rate_init, shuffle=False,
                        verbose=True, early_stopping=True
                    )
                )
            elif solver == 'adam':
                redes.append(
                    MLPClassifier(
                        hidden_layer_sizes=hidden_layer_sizes, activation=activation, solver=solver,
                        learning_rate_init=learning_rate_init, shuffle=False,
                        verbose=True, early_stopping=True
                    )
                )
                    
print(f"Quntidade de Redes: {len(redes)}")

Quntidade de Redes: 960


In [12]:
# Treinando as redes neurais
for i in range(0, len(redes)):
    print(f"\n> Rede {i}")
    redes[i].fit(X_treino, y_treino.values.ravel())

A saída de streaming foi truncada nas últimas 5000 linhas.
Iteration 4, loss = 728710072357015300984637124767645696.00000000
Validation score: 0.575199
Iteration 5, loss = 728707663910180543409199751467368448.00000000
Validation score: 0.575199
Iteration 6, loss = 728705255471303858801113268410646528.00000000
Validation score: 0.575199
Iteration 7, loss = 728702847040388936509192417507803136.00000000
Validation score: 0.575199
Iteration 8, loss = 728700438617435038663674250376773632.00000000
Validation score: 0.575199
Iteration 9, loss = 728698030202439656507364742518538240.00000000
Validation score: 0.575199
Iteration 10, loss = 728695621795403970631884611344400384.00000000
Validation score: 0.575199
Iteration 11, loss = 728693213396330194646522702000553984.00000000
Validation score: 0.575199
Iteration 12, loss = 728690805005214196480606503547437056.00000000
Validation score: 0.575199
Validation score did not improve more than tol=0.000100 for 10 consecutive epochs. Setting learning r

overflow encountered in matmul
overflow encountered in matmul


Iteration 1, loss = inf
Validation score: 0.424801
Iteration 2, loss = 60154502962123203095656945295275491752848671826755893882940266564791873627359585416106437382835238852794692878832355551048317054141329379221337535891755055769887280342202444636617225971948955507151796073050715626623531195497745778933564472719456167402984202796269568.00000000
Validation score: 0.575199


overflow encountered in matmul


Iteration 3, loss = 60154304146534292019509855463066300814351763581067576017977858772394755731248544402860701833089257480502932059583876447527679795632915133123966960592225653318519331899009557200857055242746755993786999640654431616026916812816960984446055984363880718407292798606770176.00000000
Validation score: 0.575199


...

Iteration 76, loss = inf
Validation score: 0.575199


overflow encountered in matmul


Iteration 77, loss = inf
Validation score: 0.575199


overflow encountered in matmul


A saída de streaming foi truncada nas últimas 5000 linhas.
Validation score: 0.575199
Iteration 61, loss = 0.68181402
Validation score: 0.575199
Iteration 62, loss = 0.68181402
Validation score: 0.575199
Iteration 63, loss = 0.68181402
Validation score: 0.575199
Iteration 64, loss = 0.68181402
Validation score: 0.575199
Iteration 65, loss = 0.68181402
Validation score: 0.575199
Iteration 66, loss = 0.68181402
Validation score: 0.575199
Iteration 67, loss = 0.68181401
Validation score: 0.575199
Validation score did not improve more than tol=0.000100 for 10 consecutive epochs. Setting learning rate to 0.000001
Iteration 68, loss = 0.68181392
Validation score: 0.575199
Iteration 69, loss = 0.68181392
Validation score: 0.575199
Iteration 70, loss = 0.68181392
Validation score: 0.575199
Iteration 71, loss = 0.68181392
Validation score: 0.575199
Iteration 72, loss = 0.68181392
Validation score: 0.575199
Iteration 73, loss = 0.68181392
Validation score: 0.575199
Iteration 74, loss = 0.6818139

In [13]:
# Testando as redes neurais
y_pred = []
for n, rede in enumerate(redes):
    print(f"> Rede {n}")
    y_pred.append(rede.predict(X_teste))

> Rede 0
> Rede 1
> Rede 2
> Rede 3
> Rede 4
> Rede 5
> Rede 6
> Rede 7
> Rede 8
> Rede 9
> Rede 10
> Rede 11
> Rede 12
> Rede 13
> Rede 14
> Rede 15
> Rede 16
> Rede 17
> Rede 18
> Rede 19
> Rede 20
> Rede 21
> Rede 22
> Rede 23
> Rede 24
> Rede 25
> Rede 26
> Rede 27
> Rede 28
> Rede 29
> Rede 30
> Rede 31
> Rede 32
> Rede 33
> Rede 34
> Rede 35
> Rede 36
> Rede 37
> Rede 38
> Rede 39
> Rede 40
> Rede 41
> Rede 42
> Rede 43
> Rede 44
> Rede 45
> Rede 46
> Rede 47
> Rede 48
> Rede 49
> Rede 50
> Rede 51
> Rede 52
> Rede 53
> Rede 54
> Rede 55
> Rede 56
> Rede 57
> Rede 58
> Rede 59
> Rede 60
> Rede 61
> Rede 62
> Rede 63
> Rede 64
> Rede 65
> Rede 66
> Rede 67
> Rede 68
> Rede 69
> Rede 70
> Rede 71
> Rede 72
> Rede 73
> Rede 74
> Rede 75
> Rede 76
> Rede 77
> Rede 78
> Rede 79
> Rede 80
> Rede 81
> Rede 82
> Rede 83
> Rede 84
> Rede 85
> Rede 86
> Rede 87
> Rede 88
> Rede 89
> Rede 90
> Rede 91
> Rede 92
> Rede 93
> Rede 94
> Rede 95
> Rede 96
> Rede 97
> Rede 98
> Rede 99
> Rede 100

In [14]:
acuracia = []
precisao = []
for n, pred in enumerate(y_pred):
    print(f"> Rede {n}")
    acuracia.append(acc(y_teste, pred))
    precisao.append(prec(y_teste, pred, zero_division=0.0))

> Rede 0
> Rede 1
> Rede 2
> Rede 3
> Rede 4
> Rede 5
> Rede 6
> Rede 7
> Rede 8
> Rede 9
> Rede 10
> Rede 11
> Rede 12
> Rede 13
> Rede 14
> Rede 15
> Rede 16
> Rede 17
> Rede 18
> Rede 19
> Rede 20
> Rede 21
> Rede 22
> Rede 23
> Rede 24
> Rede 25
> Rede 26
> Rede 27
> Rede 28
> Rede 29
> Rede 30
> Rede 31
> Rede 32
> Rede 33
> Rede 34
> Rede 35
> Rede 36
> Rede 37
> Rede 38
> Rede 39
> Rede 40
> Rede 41
> Rede 42
> Rede 43
> Rede 44
> Rede 45
> Rede 46
> Rede 47
> Rede 48
> Rede 49
> Rede 50
> Rede 51
> Rede 52
> Rede 53
> Rede 54
> Rede 55
> Rede 56
> Rede 57
> Rede 58
> Rede 59
> Rede 60
> Rede 61
> Rede 62
> Rede 63
> Rede 64
> Rede 65
> Rede 66
> Rede 67
> Rede 68
> Rede 69
> Rede 70
> Rede 71
> Rede 72
> Rede 73
> Rede 74
> Rede 75
> Rede 76
> Rede 77
> Rede 78
> Rede 79
> Rede 80
> Rede 81
> Rede 82
> Rede 83
> Rede 84
> Rede 85
> Rede 86
> Rede 87
> Rede 88
> Rede 89
> Rede 90
> Rede 91
> Rede 92
> Rede 93
> Rede 94
> Rede 95
> Rede 96
> Rede 97
> Rede 98
> Rede 99
> Rede 100

In [15]:
res_dict = {
    'rede': redes,
    'y_pred': y_pred,
    'acc': acuracia,
    'prec': precisao
}

In [19]:
df_resultado = pd.DataFrame.from_dict(res_dict).sort_values(by=['acc', 'prec'], ascending=False).reset_index(drop=True)
df_resultado.head()

rede  ...      prec
0  MLPClassifier(activation='relu', alpha=0.0001,...  ...  0.722222
1  MLPClassifier(activation='relu', alpha=0.0001,...  ...  0.536364
2  MLPClassifier(activation='relu', alpha=0.0001,...  ...  0.594595
3  MLPClassifier(activation='relu', alpha=0.0001,...  ...  0.530612
4  MLPClassifier(activation='relu', alpha=0.0001,...  ...  0.727273

[5 rows x 4 columns]

In [20]:
from lime.lime_tabular import LimeTabularExplainer
y_pred = lambda x: df_resultado.iloc[0]['rede'].predict_proba(x).astype(float)

desc_rede = LimeTabularExplainer(training_data=X_teste.values, feature_names=X_teste.columns, kernel_width=5)

instancia_de_dados = 5000

des_rede_saida = desc_rede.explain_instance(
    data_row=X_teste.iloc[instancia_de_dados].values, predict_fn=y_pred, num_features=10
)

print(y_teste.iloc[instancia_de_dados],"\n\n")
des_rede_saida.show_in_notebook(show_all=False)

target    0
Name: 77731, dtype: int64 


